# The instability of numerical codes: symptoms

The instability of numerical schemes and codes is one of the critical problems that a researcher using numerical experimentation may encounter. In this exercise, we are going to see how violent numerical instabilities can be.

In [1]:
# Importing relevant libraries 
%matplotlib inline
import numpy as np
import matplotlib.pyplot as plt 
from nm_lib import nm_lib as nm
from matplotlib import animation
from matplotlib.animation import FuncAnimation
from IPython.display import HTML

# plt.style.use('dark_background')
plt.style.use('default')

# Initializing constants 
x0 = -2.6 
xf =  2.6 
a = 1 

def u(x, t=False): 
    """ 
    Solves the initial condition for u(x, t=t0) from equation 2). 
    Valid when a = const 

    Parameters
    ----------
    x : `array`
       Spatial axis. 
    t : `bool`
       
    Returns
    ------- 
    `array`
        Initial condition of u(x, t=t0)
    """
    return np.cos(6*np.pi*x / 5)**2 / (np.cosh(5*x**3))

def u_exact(x, t, a): 
    r""" 
    Solves the exact solution of u(x,t) when a=const, u(x,t) = u0(x-at)

    Requires
    ----------
    Some function to define u(x,t=t0)

    Parameters
    ----------
    x : `array`
       Spatial axis. 
    t : `array`
        Time axis. 
    a : `float` or `array`
        Either constant, or array which multiply the right hand side of the Burger's eq.

    Returns
    ------- 
    uu : `array`
        Spatial and time evolution of u(x,t) = u0(x-at)
    """
    
    xx = np.zeros((len(x), len(t)))
    x_tmp = np.zeros((len(x), len(t)))

    for i in range(0, len(t)): 
        # Sets boundaries using mod (bring solution back into domain)
        # Taking mod of the length of the grid (2.6) returns the remainder of the divide 
        # -> The right column and row         
        x_tmp[:,i] = ((x - a*t[i]) - x0) % (xf - x0) + x0 

        # Insert into u0
        xx[:,i]    = u(x_tmp[:,i]) # u0(x-at)
    return xx


## 1 – Numerical instability: violent development

1. Repeat the numerical simulation carried out __in exercise [ex_2a](https://github.com/AST-Course/AST5110/blob/main/ex_2a.ipynb)__, but now take $a = 1$ (it was $a = −1$); (use a moderate number of intervals, like, e.g., 128). Check out what happens. After how many timesteps does instability become evident?

In [2]:
# Initialize xx, t and unnt 
nint = 128 
nump = nint + 1
nt = 100
xx = np.arange(nump)/(nump-1.0) * (xf - x0) + x0
t, unnt = nm.evolv_adv_burgers(xx, u(xx), nt, a)
unnt_exact = u_exact(xx, t, a)

N = 5
# Animation 
fig, axes = plt.subplots(nrows=1, ncols=1, figsize=(10, 5))

def init(): 
    xx,unnt[:,::N][:,0]

def animate(i):
    axes.clear()
    axes.plot(xx,unnt[:,::N][:,i])
    axes.set_title('t=%.2f'%t[i])
    # axes.set_ylim((0,1.05))
    axes.grid(True)
    
anim = FuncAnimation(fig, animate, interval=50, frames=len(t[::N]), init_func=init)
plt.close()
HTML(anim.to_jshtml())

<span style="color:pink">

The instability is evident from the first timestep. 

</span>

Repeat the experiment with 1024 points (and afterward with any other power of 2 you may want to use). Is the experiment stable now? After how many timesteps does the instability become evident now?

<span style="color:green">JMS</span>.

In [3]:
# Initialize xx, t and unnt 
nint = 1024
nump = nint + 1
nt = 200
xx = np.arange(nump)/(nump-1.0) * (xf - x0) + x0
t, unnt = nm.evolv_adv_burgers(xx, u(xx), nt, a)
unnt_exact_1024 = u_exact(xx, t, a)

N = 7
# Animation 
fig, axes = plt.subplots(nrows=1, ncols=1, figsize=(10, 5))

def init(): 
    xx, unnt[:,::N][:,0]

def animate(i):
    axes.clear()
    axes.plot(xx, unnt[:,::N][:,i])
    axes.set_title('t=%.2f'%t[i])
    # axes.set_ylim((0,1.05))
    axes.grid(True)
    
anim = FuncAnimation(fig, animate, interval=50, frames=len(t[::N]), init_func=init)
plt.close()
HTML(anim.to_jshtml())

<span style="color:pink">

The solution becomes unstable for an earlier timestep when the number of intervals is lower. 

The upwind method works by approximating the solution at a point in space and time using information from the points upstream (or upwind) of that point. 

When the velocity $a$ is positive, the upwind method approximates the solution using information from the upstream points, which are in the same direction as the flow. In this case, the method works well. 
However, when the velocity is negative, the upwind method uses information from the downstream points, which are in the opposite direction to the flow. This may lead to numerical oscillations and instability in the solution, particularly in regions of high gradients. 

To address this issue, we use the downwind method when the velocity is negative. This method approximates the solution using information from the downstream points, which are then in the same direction as the flow, providing a more stable and accurate solution for that case. 

</span>



2. Still for $a = 1$, use for the spatial differentiation backward finite differencing, i.e.:

$$\left(\frac{\partial u}{\partial x}\right)_{x=x_i} \rightarrow \frac{u_i-u_{i-1}}{\Delta x}  \tag{1}$$

Fill in the `nm_lib` function `deriv_upw`, and use the `lambda` function `ddx` and select the proper limits for `bnd_limits`. 

In [4]:
nt = 200
t, unnt = nm.evolv_adv_burgers(xx, u(xx), nt, a, \
    ddx = lambda x,y: nm.deriv_upw(x, y), bnd_limits=[1,0])

N = 5
# Animation 
fig, axes = plt.subplots(nrows=1, ncols=1, figsize=(10, 5))

def init(): 
    axes.plot(xx, unnt[:,::N][:,0])

def animate(i):
    axes.clear()
    axes.plot(xx,unnt[:,::N][:,i])
    axes.set_title('t=%.2f'%t[i])
    axes.set_ylim((0,1.05))
    axes.grid(True)
    
anim = FuncAnimation(fig, animate, interval=1, frames=len(t[::N]), init_func=init)
plt.close()
HTML(anim.to_jshtml())

__taking care of also changing the implementation of the boundary condition.__ Does the unstable character of the code change?

<span style="color:pink">

The solution is stable when using a backward-oriented finite-difference scheme, indicating that when $a>0$, this scheme yields stability. 

</span>

## 2 – Centered differences

Use now for the spatial derivation _centered finite differences_, i.e.:

$$\left(\frac{\partial u}{\partial x}\right)_{x=x_i} \rightarrow \frac{u_{i+1}-u_{i-1}}{2\Delta x}   \tag{2}$$

(and see the note on boundary conditions below). Fill in `nm_lib` the function `deriv_cent`, and like in the previous case, use the `lambda` function `ddx` and select the proper limits for `bnd_limits`. Use `cfl_cut=0.3`. Is any instability apparent in this case? Does the situation change when you change the sign of the constant $a$?

Note: In this case, the periodicity boundary condition can be implemented as follows: define $xx$ so that the endpoint $x = x_0$ of the domain coincides with $xx[1]$ (i.e., the second component of the array) and the endpoint $x = x_f$ coincides with the last element in the array [i.e., $xx[nump-1]$]. For the boundary condition, you can do the following: assume you are calling $uun$ the array at time $t + \Delta t$. Then the boundary condition is imposed by specifying $uun[0] = uun[nump-2]$ and $uun[nump-1] = uun[1]$.

In [5]:
# Initialize xx, t and unnt 
nint = 128
nump = nint + 1
xx = np.arange(nump)/(nump-1.0) * (xf - x0) + x0

t, unnt = nm.evolv_adv_burgers(xx, u(xx), nt=200, a=1, cfl_cut=0.3, \
    ddx = nm.deriv_cent, bnd_limits=[1,1], bnd_type='wrap')

N = 10 
# Animation 
fig, axes = plt.subplots(nrows=1, ncols=1, figsize=(10, 5))

def init(): 
    xx, unnt[:,::N][:,0]

def animate(i):
    axes.clear()
    axes.plot(xx, unnt[:,::N][:,i])
    axes.set_title('t=%.2f'%t[i])
    # axes.set_ylim((0,1.05))
    axes.grid(True)

anim = FuncAnimation(fig, animate, interval=50, frames=len(t[::N]), init_func=init)
plt.close()
HTML(anim.to_jshtml())

<span style="color:pink">

The solution starts to blow up and becomes unstable after a few timesteps. This is the case for both $a=1$ and $a=-1$. 

</span>

## 3 – The stability of the non-centered finite-differences schemes

In the previous exercises, we saw that when $a > 0$, a _backward-oriented_ finite-difference scheme yields stability. However, a crucial component in the problem was to give a specific value for $\Delta t$, namely  $t = 0.98 x/|a|$. Would it have been wise to choose a larger or smaller $\Delta t$? Let us check that $\Delta t$ cannot be chosen arbitrarily large: run the program, but now writing

1. $\Delta t = 0.5 \frac{\Delta x}{a}$;
2. $\Delta t = 0.99 \frac{\Delta x}{a}$;
3. $\Delta t = 1.01 \frac{\Delta x}{a}$;
4. $\Delta t = 2 \frac{\Delta x}{a}$;

and check if those values maintain the good stability properties of the code. For example, does there seem to be a threshold in $\Delta t$ for the instability? Note that you need to define `cfl_cut` to 0.5, 0.99, 1.01, and 2.0.

In [6]:
nint = 128 
nump = nint + 1
xx = np.arange(nump)/(nump-1.0) * (xf - x0) + x0

dt_list = [0.5, 0.99, 1.01, 2]

N = 10
def ani(dt): 
    t, unnt = nm.evolv_adv_burgers(xx, u(xx), nt=150, a=1, cfl_cut=dt, \
        ddx = lambda x,y: nm.deriv_upw(x, y), bnd_limits=[1,0])

    # Animation 
    fig, axes = plt.subplots(nrows=1, ncols=1, figsize=(10, 5))

    def init(): 
        xx, unnt[:,::N][:,0]

    def animate(i):
        axes.clear()
        axes.plot(xx, unnt[:,::N][:,i])
        axes.set_title('t=%.2f'%t[i])
        axes.set_ylim((0,1.05))
        axes.grid(True)

    anim = FuncAnimation(fig, animate, interval=50, frames=len(t[::N]), init_func=init)
    plt.close()
    return anim
    # HTML(anim.to_jshtml())

In [7]:
anim = ani(dt_list[0])
HTML(anim.to_jshtml())

<span style="color:pink">

The solution is stable, but not a very good fit after a few timesteps, as it begins to diffuse. 

</span>

In [8]:
anim = ani(dt_list[1])
HTML(anim.to_jshtml())

<span style="color:pink">

This solution is more stable than the previous, showing less diffusion. 

</span>

In [9]:
anim = ani(dt_list[2])
HTML(anim.to_jshtml())

<span style="color:pink">

This solution will become unstable, as can be seen from the increasing amplitude. 

</span>

In [10]:
anim = ani(dt_list[3])
HTML(anim.to_jshtml())

<span style="color:pink">

This solution quickly becomes unstable. 

</span>

<span style="color:pink">

The solution becomes unstable for $\Delta t > 1$, but will be innacurate if $\Delta t$ is too low. 

For the central scheme we used dt = 0.3, rather than dt = 0.9. The central scheme has twice the stepsize, and therefore needs a lower dt before it becomes unstable. 

</span>

<span style="color:green">JMS</span>.

<span style="color:blue">Great job! All the above looks good</span>.

## 4- Optional (A). 

Consider now the following Burgers’ equation, i.e.,

$$\frac{\partial u}{\partial t} + u \frac{\partial u}{\partial x} = 0   \tag{3}$$

can be seen as yet another case of the equation solved in the previous exercises of this
series by writing:

$$a(x,t,u) = u  \tag{4}$$

The importance of this equation in physics derives in part from the fact that it describes
the motion of a non-accelerated fluid with an arbitrary velocity field at time $t = 0$ and
because it contains the possibility of spontaneous formation of discontinuities. (\*)

We can simply solve equation (1) by modifying the program developed for the previous exercises but now writing $a(x_i, t^n) = u^n_i$. Carry out that modification, and run the program in the domain $x \in (x_0, x_f)$ with $x_0 = −1.4$, $x_f = 2.0$ with the initial condition:

$$u(x,t=0) = A\left[\tanh\left(\frac{x+x_c}{W}\right)-\tanh\left(\frac{x-x_c}{W}\right) \right] + B \tag{5}$$

whereby $A = 1.0$, $x_c = 0.70$, $W = 0.1$, $B = 0.3$. Let the solution evolve until time $t_f = 100$. Explain in physical (or mathematical) terms the solution you get. Change to $A = −0.02$ and explain the result. For this exercise, fill in `nm_lib` functions `evolv_uadv_burgers` and `step_uadv_burgers`. 

In [11]:
def u(x, A=1.0): 
    """         
    Initial condition for t=t0 when a = const

    Parameters
    ----------
    x : `array`
        Spatial axis. 
    A : `float`
        A constant of the initial condition (default = 1.0).
    
    Returns
    -------
    Equation 2
    """ 
    xc = 0.70
    W = 0.1 
    B = 0.3
    return A*(np.tanh((x+xc) / W) - np.tanh((x-xc) / W)) + B

x0 = -1.4 
xf = 2.0 

nint = 128 
# nint = 1024
nump = nint + 1
xx = np.arange(nump)/(nump-1.0) * (xf - x0) + x0

In [12]:
t, unnt = nm.evolv_uadv_burgers(xx, u(xx), nt=2000, cfl_cut = 0.4)
N = 100

# Animation 
fig, axes = plt.subplots(nrows=1, ncols=1, figsize=(10, 5))

def init(): 
    axes.plot(xx, unnt[:,::N][:,0])

def animate(i):
    axes.clear()
    axes.plot(xx, unnt[:,::N][:,i])
    axes.set_title('t=%.2f'%t[i])
    axes.grid(True)
    
anim = FuncAnimation(fig, animate, interval=50, frames=len(t[::N]), init_func=init)
plt.close()
HTML(anim.to_jshtml())

/home/semya/cs/AST5110/nm_lib/nm_lib/nm_lib.py:239: RuntimeWarning: overflow encountered in multiply
  rhs = -a*ddx(xx, hh)
/home/semya/cs/AST5110/nm_lib/nm_lib/nm_lib.py:351: RuntimeWarning: invalid value encountered in multiply
  unnt_temp = unnt[:, i] + rhs*dt


In [13]:
t, unnt = nm.evolv_uadv_burgers(xx, u(xx, A=-0.02), nt=2000, cfl_cut = 0.4)
N = 100

# Animation 
fig, axes = plt.subplots(nrows=1, ncols=1, figsize=(10, 5))

def init(): 
    axes.plot(xx, unnt[:,::N][:,0])

def animate(i):
    axes.clear()
    axes.plot(xx, unnt[:,::N][:,i])
    axes.set_title('t=%.2f'%t[i])
    axes.grid(True)
    
anim = FuncAnimation(fig, animate, interval=50, frames=len(t[::N]), init_func=init)
plt.close()
HTML(anim.to_jshtml())

/home/semya/cs/AST5110/nm_lib/nm_lib/nm_lib.py:239: RuntimeWarning: overflow encountered in multiply
  rhs = -a*ddx(xx, hh)
/home/semya/cs/AST5110/nm_lib/nm_lib/nm_lib.py:351: RuntimeWarning: invalid value encountered in multiply
  unnt_temp = unnt[:, i] + rhs*dt


<span style="color:pink">

When A = 1.0, the function has an initial amplitude of 2.25, while the graph is upside down with an amplitude of 0.260 when A = -0.02. 

The solution becomes unstable in both cases. 

</span>

### Comments:

In the numerical solution, we see the initial condition patently evolving into something that looks like a discontinuity. We understand that this discontinuity is formed because the characteristic curves $dx_p/dt = a(x, t, u) = u$ are more inclined (i.e., faster) in a spacetime diagram when starting at elements with larger $u$: since the solution is constant along those curves, the faster elements, therefore, catch those in front of them which have lower $u$ (as is the case in the solution you have found numerically here) – so the solution must steepen when that happens.

Mathematically and physically, we should not be too surprised: we know that, for instance, in gas dynamics, weird nonlinear phenomena take place, some of which (the shocks) have to do with the formation of discontinuities or sharp transitions. Numerically, though, we ought to be rather surprised for various reasons:
    
a. the numerical calculation of a very large value of the derivative (as is surely the case across the big jump forming in our calculation) cannot be very accurate. It might even happen, we think, that the program crashed because of _NaNs_ or exceptions, etc, occurring in the calculation. But, in fact, our program happily calculates away ... seemingly forever.

b. when a discontinuity forms, the exact mathematical solution, strictly speaking, cannot be calculated in a simple way anymore: when there is a discontinuity, one must take into account what is called the jump relations, also called internal boundary conditions, across the discontinuity: they give the mutual relation of the variables on either side of the discontinuity. A solution obtained in this way is called a __weak solution__ in mathematics.

c. we finally ask ourselves what the mathematically-exact weak solution would be in this case and whether our simple numerical scheme provides a solution near the exact one despite the obvious difficulty of handling large jumps across the near-discontinuity.

We have to leave these as open questions for discussion at a later point. 

As a final comment, consider the consequences of the fact that the acceleration in gas dynamics contains a term of the general form $u$ $du/dx$ .... Much of the beautiful physics occurring in the universe is due to non-linearities like this one.

## 4- Optional (B) 

For this exercise, do first [ex_4a](https://github.com/AST-Course/AST5110/blob/main/ex_4a.ipynb). 
Consider the same setup as the previous exercise. But now, solve it using the upwind method: 

$$u^{n+1}_j = u^{n}_j - \frac{\Delta t}{\Delta x} u^{n}_j(u^{n}_j- u^{n}_{j+1})$$

And using the Lax method implemented in [ex_4a](https://github.com/AST-Course/AST5110/blob/main/ex_4a.ipynb). What do you see? Argue why you think the solution is not correct. __Hint__ In the first exercise, we disccused about flux conservation.

In [14]:
t_upwind, unnt_upwind = nm.evolv_uadv_burgers(xx, u(xx), nt, ddx=nm.deriv_upw, bnd_limits=[1,0])
t_lax, unnt_lax = nm.evolv_Lax_uadv_burgers(xx, u(xx), nt, ddx=nm.deriv_upw, bnd_limits=[1,0])

same_t = np.where(np.isclose(t_lax, t_upwind, atol=5e-1))[0] # Commin times 
t = t_lax[same_t]

N = 10
# Animation 
fig, axes = plt.subplots(nrows=1, ncols=1, figsize=(10, 5))

def init(): 
    axes.plot(xx, unnt_upwind[:,::N][:,0])
    axes.plot(xx, unnt_lax[:,::N][:,0])

def animate(i):
    axes.clear()
    axes.plot(xx, unnt_upwind[:,::N][:,same_t[i]], label='Upwind')
    axes.plot(xx, unnt_lax[:,::N][:,same_t[i]], label='Lax')
    axes.legend()
    axes.set_ylim((0, 2.5))
    axes.set_title('t=%.2f'%t[::N][same_t[i]])
    axes.grid(True)
    
anim = FuncAnimation(fig, animate, interval=50, frames=len(t[::N]), init_func=init)
plt.close()
HTML(anim.to_jshtml())

<span style="color:pink">

Both the upwind and Lax method can be used to solve Burgers' equation. The Upwind method is simple and computationally efficient, it can lead to numerical instabilities and oscillations in the solution, particularly in regions of high gradients or when the flow is discontinuous. The Lax method, is a more sophisticated numerical method that uses a combination of forward and backward time-stepping and a central difference approximation for the advection term in Burgers' equation. This results in a second-order accurate method that is more stable and less prone to numerical oscillations than the upwind Burgers method. The Lax method is also more computationally expensive than the upwind Burgers method, but can provide more accurate solutions, particularly for problems with steep gradients or discontinuities. 

For the Upwind method $u_i(u_i + u_{i-1})$ the parenthesis is defined in $i+1/2$, while outside the parenthisis it is defined at $i$. This makes the method non-conservative and produces a phase error, meaning that it moves slower than the shock. This can be fixed by changing 

$$
    u \frac{\partial u}{\partial x} \rightarrow \frac{\partial u^2/2}{\partial x}, 
$$

which makes everything be defined in the same place. 

For the Lax method we define the variable sin a staggered mesh (?) which allows preserving the PDEs' conservation. 

</span>

<span style="color:green">JMS.</span>.

<span style="color:blue">Great you did both optional excercises!</span>.

<span style="color:blue">Great job! And you explanation is close. In the upwind method $u_i (u_i+u_{i-1})$ makes the parenthesis to be defined in i+1/2 but outside the parenthesis is at i. So this makes this method non-conservative and produces a phase error. In other words, it is moving slower the shock. This could be fixed if instead of doing  $u \frac{\partial u}{\partial x}$, do $\frac{\partial u^2/2}{\partial x}$, then everything will be defined in the same place. </span>. 

<span style="color:yellow"> I would like to make sure that you understand my explanation above.


### Comments:
    
See [Stagger mesh](https://github.com/AST-Course/AST5110/wiki/Staggered-mesh) documentation on how a staggered mesh allows keeping the conservation. 